In [ ]:
from datasets import load_dataset

In [ ]:
data_files = {
    "train": "./train.txt",
    "val": "./val.txt",
    "test": "./test.txt",
}
ds = load_dataset("text", data_files=data_files)

In [ ]:
ds['train'] = ds['train'].rename_column('text', 'SMILE')
ds['val'] = ds['val'].rename_column('text', 'SMILE')
ds['test'] = ds['test'].rename_column('text', 'SMILE')

In [ ]:
import selfies as sf

def try_convert(row):
    selfie = None
    try:
        selfie = sf.encoder(row['SMILE'])
    except:
        pass

    return {'SELFIE': selfie}

# Alongside the SMILES, we also need to convert them to SELFIES
# ds['train'] = ds['train'].add_column('SELFIE', ds['train'].map(try_convert, num_proc=8))

In [ ]:
ds['train'] = ds['train'].map(try_convert, num_proc=8)
ds['val'] = ds['val'].map(try_convert, num_proc=8)
ds['test'] = ds['test'].map(try_convert, num_proc=8)

In [ ]:
# Drop the rows where the conversion failed
ds['train'] = ds['train'].filter(lambda row: row['SELFIE'] is not None)
ds['val'] = ds['val'].filter(lambda row: row['SELFIE'] is not None)
ds['test'] = ds['test'].filter(lambda row: row['SELFIE'] is not None)

In [ ]:
from tokenizers import Tokenizer

tokenizer = Tokenizer.from_pretrained("haydn-jones/GuacamolSELFIETokenizer")

In [ ]:
unk_id = tokenizer.token_to_id('<UNK>')

# Drop any rows where the tokenization has an <UNK> token
ds['train'] = ds['train'].filter(lambda row: unk_id not in tokenizer.encode(row['SELFIE']).ids, num_proc=8)
ds['val'] = ds['val'].filter(lambda row: unk_id not in tokenizer.encode(row['SELFIE']).ids, num_proc=8)
ds['test'] = ds['test'].filter(lambda row: unk_id not in tokenizer.encode(row['SELFIE']).ids, num_proc=8)

In [ ]:
ds.save_to_disk('./guacamol')

In [ ]:
repo_id = "haydn-jones/Guacamol"

# Push the dataset to the repo
ds.push_to_hub(repo_id)